# Notebook Objective and Setup

BGG05 is the building of a content-based item filter. Using category weights, I use my domain expertise to tune an item similarity matrix for all game IDs in the games file.

This content-based filter could be used as-is to find similar games to a user's catalog and predict ratings.

## Notebook Preparation

### Package Imports

In [1]:
import pandas as pd
import numpy as np
import requests
import regex as re
import time
import os
import gc
import copy
import json

# ignore warnings (gets rid of Pandas copy warnings)
import warnings
warnings.filterwarnings('ignore')
pd.options.display.max_columns = None

pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', 30)

from sklearn.metrics.pairwise import cosine_similarity
from sklearn.preprocessing import MinMaxScaler, OneHotEncoder
from missingpy import MissForest
from sklearn.pipeline import Pipeline
from sklearn.compose import ColumnTransformer
from sklearn.feature_extraction.text import TfidfTransformer

# NLP tools
import spacy
nlp = spacy.load("en_core_web_sm")
import re
import nltk
import fasttext
from sklearn.feature_extraction.text import CountVectorizer, TfidfVectorizer
from nltk.tokenize import word_tokenize
from tensorflow.keras.preprocessing.text import Tokenizer
from tensorflow.keras.preprocessing.sequence import pad_sequences
from tensorflow.python.keras.preprocessing import sequence, text

### Notebook Functions

##### Processing Functions

In [37]:
def processing_pipeline(weight_groups, df):
    '''
    !!!Hard-coded processor!!!
    Takes in weight tuples and a dataframe
    Scales specific dataframe columns to tuples
    
    Inputs:
    weight_groups: list of weight tuples (x, y)
    df: df to be scaled
    
    Returns:
    Processed Dataframe'''

   
    # continuous pipeline
    family_encoder = Pipeline([
        ('encoder', OneHotEncoder()),
        ('scaler', MinMaxScaler(feature_range=weight_groups[6])),
         ])
    
    # Whole pipeline with continuous then categorical transformers
    total_pipeline = ColumnTransformer([
        ('games_weight_weight', MinMaxScaler(feature_range=weight_groups[0]), ['GameWeight']),
        ('avgrating', MinMaxScaler(feature_range=weight_groups[1]), ['AvgRating']),
        ('bayes_weight', MinMaxScaler(feature_range=weight_groups[2]), ['BayesAvgRating']),  
        ('players_weight', MinMaxScaler(feature_range=weight_groups[3]), ['BestPlayers']),
        ('playtime_weight', MinMaxScaler(feature_range=weight_groups[4]), ['Playtime']),
        ('remainder_weight', MinMaxScaler(feature_range=weight_groups[5]), [ 'Cat:War',
                       'Cat:CGS','Cat:Abstract','Cat:Party','Cat:Childrens']),
                            ]) 
    
    # Fit and tranform the pipeline on x_train, then transform x_test
    processed = total_pipeline.fit_transform(df)
    
    return processed

In [3]:
def scale_dataset(dataset, weights, tfidf=False):
    '''
    Set each item either according to Term Frequency or TF-IDF
    Then scale dataset according to provided weights
    
    tfidf flag:
    Use TRUE when RARE entries are more important than FREQUENT entries
    Use FALSE when COMMON entries are more important than RARE entries
    
    Inputs:
    dataset: dataset to scale
    weights: tuple (x, y) to weight dataset
    tfidf: set flag to True for TF-IDF
    
    Outputs:
    Scaled data
    '''
    
    # drop BGG Id
    try: 
        dataset_pared = dataset.drop('BGGId', axis=1)
    except: 
        dataset_pared = dataset
    
    # get list of titles to reapply to DF after transformation
    titles = list(dataset_pared.columns)

    # set up weighted scaler
    scaler = MinMaxScaler(feature_range = weights)
    
    # get total number of entries
    total_entries = sum(dataset.sum())
    
    if tfidf:
        
        #instantiate tfidf transformer
        tfidf = TfidfTransformer()
    
        #convert matrix to tfidf 
        tfidf_dataset = pd.DataFrame(tfidf.fit_transform(dataset_pared).toarray(), columns=titles)
        
        # run scaler on transpose (scale by row not column)
        transpose_scaled = scaler.fit_transform(tfidf_dataset.T)
        
    else:
        # for each column,
        for item in list(dataset_pared.columns):
            # set item as its term frequency
            dataset_pared.loc[dataset_pared[item]>0, item] = dataset_pared[item].sum()/total_entries
    
        # run scaler on transpose (scale by row not column)
        transpose_scaled = scaler.fit_transform(dataset_pared.T)
    
    # rebuild dataframe
    scaled_dataset = pd.DataFrame(transpose_scaled.T, columns=titles)
    
    return scaled_dataset


# Content Based Filtering

## Set Weights

These are the scales for each of these categories. All entries in the category will be scaled to this tuple range by the MinMaxScaler.

In [4]:
### DO NOT TOUCH THESE ARE THE PRODUCTION WEIGHTS!!!!!

games_weight_weight = (-1.5, 1.5) # game weight. Is a range, so (-, )
rating_weight = (-.3, .3)
bayes_weight = (-.5, .5) # game weighted rating. Is a range, so (-, )
players_weight = (0, 1) # best players. Is a problematic range due to outliers
playtime_weight = (0, 2) # playtime. Is a range so (-, ). Has high outliers
designers_weight = (0, 0.5) # designers, binary
mechanics_weight = (0, .75) # mechanics, binary
subcategories_weight = (0, .75) # other mechanics like card game, print&play. binary
family_weights = (0, 0.5) # game families like pandemic, century. binary
categories_weight = (0, 1) # the five large overarching categories, binary
themes_weight = (-.15, 0.15) # themes like space, western. binary

'games_weight_weight = (-1.5, 1.5) # game weight. Is a range, so (-, )\nrating_weight = (-.3, .3)\nbayes_weight = (-.5, .5) # game weighted rating. Is a range, so (-, )\nplayers_weight = (0, 1) # best players. Is a problematic range due to outliers\nplaytime_weight = (0, 2) # playtime. Is a range so (-, ). Has high outliers\ndesigners_weight = (0, 0.5) # designers, binary\nmechanics_weight = (0, .75) # mechanics, binary\nsubcategories_weight = (0, .75) # other mechanics like card game, print&play. binary\nfamily_weights = (0, 0.5) # game families like pandemic, century. binary\ncategories_weight = (0, 1) # the five large overarching categories, binary\nthemes_weight = (-.15, 0.15) # themes like space, western. binary'

In [ ]:
'''games_weight_weight = (-1, 1) # game weight. Is a range, so (-, )
rating_weight = (-.5, .5)
bayes_weight = (-.001, .001) # game weighted rating. Is a range, so (-, )
players_weight = (0, 1) # best players. Is a problematic range due to outliers
playtime_weight = (0, 2) # playtime. Is a range so (-, ). Has high outliers
designers_weight = (0, 0.5) # designers, binary
mechanics_weight = (0, .75) # mechanics, binary
subcategories_weight = (0, .75) # other mechanics like card game, print&play. binary
family_weights = (0, 0.5) # game families like pandemic, century. binary
categories_weight = (0, 1) # the five large overarching categories, binary
themes_weight = (-.15, 0.15) # themes like space, western. binary'''

## Load and Prep Data

In [93]:
# Load games
games = pd.read_pickle('data_cleaned_new_scraper/games.pkl')

# determine playtime for each game according to community
games['Playtime'] = 0
games['Playtime'] = games.apply(lambda x: np.mean(x['ComMinPlaytime'] + x['ComMaxPlaytime']), axis=1)

# set upper cap on playtime
over_6_hours = list(games.loc[games['Playtime']>360].index)
games.loc[over_6_hours, 'Playtime']=360

# load other files to use
mechanics = pd.read_pickle('data_cleaned_new_scraper/mechanics.pkl')
designers = pd.read_pickle('data_cleaned_new_scraper/designers_reduced.pkl')
subcategories = pd.read_pickle('data_cleaned_new_scraper/subcategories.pkl')
themes = pd.read_pickle('data_cleaned_new_scraper/themes.pkl')

#games.head()

### TF-IDF

In [76]:
# Load spaCy with English language processor
nlp = spacy.load("en_core_web_sm")

In [8]:
descriptions = games[['Description']]
descriptions.head()

Description
0  die macher game seven sequential political rac...
1  dragonmaster tricktaking card game base old ga...
2  samurai set medieval japan player compete gain...
3  triangular box luxurious large block tal der k...
4  acquire player strategically invest business t...

In [9]:
# prepare the vectorizer with the chosen parameters
tfid_proc = TfidfVectorizer(sublinear_tf=True, use_idf=True, max_df=0.8, min_df=.005, ngram_range=(1,3), max_features=5000)

# fit the vectorizer to the train data, transform train and holdout
word_vectors = tfid_proc.fit_transform(descriptions['Description'])

# cast the vector array to a data frame with columns named by the features selected by the vectorizer
word_vectors = pd.DataFrame(word_vectors.toarray(), columns=tfid_proc.get_feature_names())


In [10]:
word_vectors.head()

abandon  ability  able  abstract  abstract strategy  accept  access  \
0      0.0      0.0   0.0       0.0                0.0     0.0     0.0   
1      0.0      0.0   0.0       0.0                0.0     0.0     0.0   
2      0.0      0.0   0.0       0.0                0.0     0.0     0.0   
3      0.0      0.0   0.0       0.0                0.0     0.0     0.0   
4      0.0      0.0   0.0       0.0                0.0     0.0     0.0   

   accessible  accomplish  accord  account  accumulate  accurate  ace  \
0         0.0         0.0     0.0      0.0         0.0       0.0  0.0   
1         0.0         0.0     0.0      0.0         0.0       0.0  0.0   
2         0.0         0.0     0.0      0.0         0.0       0.0  0.0   
3         0.0         0.0     0.0      0.0         0.0       0.0  0.0   
4         0.0         0.0     0.0      0.0         0.0       0.0  0.0   

   achieve   acquire  act  action  action card  action player  action point  \
0      0.0  0.000000  0.0     0.0          0.0            0.0           0.0   
1      0.0  0.000000  0.0     0.0          0.0            0.0           0.0   
2      0.0  0.000000  0.0     0.0          0.0            0.0           0.0   
3      0.0  0.000000  0.0     0.0          0.0            0.0           0.0   
4      0.0  0.191209  0.0     0.0          0.0            0.0           0.0   

   action turn  activate  activation  active  active player  activity  actual  \
0          0.0       0.0         0.0     0.0            0.0       0.0     0.0   
1          0.0       0.0         0.0     0.0            0.0       0.0     0.0   
2          0.0       0.0         0.0     0.0            0.0       0.0     0.0   
3          0.0       0.0         0.0     0.0            0.0       0.0     0.0   
4          0.0       0.0         0.0     0.0            0.0       0.0     0.0   

   actually   ad  adapt       add  add card  add new  addition  additional  \
0  0.000000  0.0    0.0  0.066942       0.0      0.0       0.0    0.086164   
1  0.000000  0.0    0.0  0.000000       0.0      0.0       0.0    0.000000   
2  0.000000  0.0    0.0  0.000000       0.0      0.0       0.0    0.000000   
3  0.000000  0.0    0.0  0.000000       0.0      0.0       0.0    0.000000   
4  0.063882  0.0    0.0  0.000000       0.0      0.0       0.0    0.000000   

   additionally  adjacent  adjust  adult  advance  advanced  advanced rule  \
0           0.0       0.0     0.0    0.0      0.0       0.0            0.0   
1           0.0       0.0     0.0    0.0      0.0       0.0            0.0   
2           0.0       0.0     0.0    0.0      0.0       0.0            0.0   
3           0.0       0.0     0.0    0.0      0.0       0.0            0.0   
4           0.0       0.0     0.0    0.0      0.0       0.0            0.0   

   advantage  adventure  adventure game  adventurer  affect  africa  age  \
0        0.0        0.0             0.0         0.0     0.0     0.0  0.0   
1        0.0        0.0             0.0         0.0     0.0     0.0  0.0   
2        0.0        0.0             0.0         0.0     0.0     0.0  0.0   
3        0.0        0.0             0.0         0.0     0.0     0.0  0.0   
4        0.0        0.0             0.0         0.0     0.0     0.0  0.0   

   agent  ago  agree  ahead   ai  aid  aid card  aim  aim game  air  aircraft  \
0    0.0  0.0    0.0    0.0  0.0  0.0       0.0  0.0       0.0  0.0       0.0   
1    0.0  0.0    0.0    0.0  0.0  0.0       0.0  0.0       0.0  0.0       0.0   
2    0.0  0.0    0.0    0.0  0.0  0.0       0.0  0.0       0.0  0.0       0.0   
3    0.0  0.0    0.0    0.0  0.0  0.0       0.0  0.0       0.0  0.0       0.0   
4    0.0  0.0    0.0    0.0  0.0  0.0       0.0  0.0       0.0  0.0       0.0   

   aka   al  alien  alike  alive  alliance  allied  allocate  allow  \
0  0.0  0.0    0.0    0.0    0.0       0.0     0.0       0.0    0.0   
1  0.0  0.0    0.0    0.0    0.0       0.0     0.0       0.0    0.0   
2  0.0  0.0    0.0    0.0    0.0       0.0     0.0       0.0  

In [11]:
word_vectors.shape

(21925, 2539)

Load in the description vectors (produced and saved in the appendix)

In [30]:
description_vectors = pd.read_pickle('data_cleaned_new_scraper/description_vectors.pkl')

In [31]:
description_vectors.shape

(21925, 26699)

### Weight Scale Datasets

##### TF-IDF Mechanics

In [94]:
# get floor of mechanics presence in catalog (.05% of games)
mechanics_floor = round(mechanics.shape[0]*.005)

# make a list of mechanics more than the floor
sums = pd.DataFrame(mechanics.sum()>=mechanics_floor)

# get indices for the mechanics keeping
keep_mechanics = sums.loc[sums[0]==True].index

refined_mechanics = mechanics[keep_mechanics]

# scaled mechanics
scaled_mechanics = scale_dataset(refined_mechanics, mechanics_weight, tfidf=True)

# make new column for games without any mechanics information
no_mechanics_index = list(scaled_mechanics.loc[scaled_mechanics.sum(axis=1)==0].index)
scaled_mechanics['No Mechanics'] = 0
scaled_mechanics.loc[no_mechanics_index, 'No Mechanics'] = (mechanics_weight[1])

##### TF-Scale Only Datasets

In [95]:
# scale themes
scaler = MinMaxScaler(feature_range=themes_weight)
scaled_themes = scaler.fit_transform(themes)

# get list of titles to reapply to DF after transformation
titles = list(themes.columns)  

scaled_themes = pd.DataFrame(scaled_themes, columns=titles)
scaled_themes.drop('BGGId', axis=1, inplace=True)

# scaled designers
scaled_designers = scale_dataset(designers, designers_weight)

# scaled game families
game_families = pd.get_dummies(games['Family'])
scaled_families = scale_dataset(game_families, family_weights)

#scaled subcategories
scaled_subcategories = scale_dataset(subcategories, subcategories_weight)

### Master CBF Frame

In [96]:
# include these columns for comparison
games_included_columns = ['GameWeight', 'AvgRating', 'BayesAvgRating', 'BestPlayers', 'Playtime', 'Cat:War', 'Cat:CGS', 'Cat:Abstract', 'Cat:Party', 'Cat:Childrens'] 

# make smaller df of the included columns
scaled_games = games[games_included_columns]

# get list of game names
game_names = list(games['Name'])
# get list of game ids
game_ids = list(games['BGGId'])

# create game lookup table
game_lookup = {}
for key, value in zip(game_ids, game_names):
    game_lookup[key] = value

# instantiate MissForest imputer and fill all nans in scaled_games
imputer = MissForest()
scaled_games = pd.DataFrame(imputer.fit_transform(scaled_games), columns=games_included_columns)

In [97]:
# set up weight groups for hard coded pipeline
weight_groups = [games_weight_weight, rating_weight, bayes_weight, players_weight, playtime_weight, categories_weight, family_weights]

# process scaled_games with pipeline
scaled_games = pd.DataFrame(processing_pipeline(weight_groups, scaled_games), columns=games_included_columns)

# make list of games and ids (is this used anywhere?)
game_and_id = list(zip(game_names, game_ids))

In [98]:
# put together master dataframe with other already processed dataframes
master_games = pd.concat((scaled_games, scaled_themes, scaled_mechanics, scaled_families, scaled_designers, scaled_subcategories, description_vectors, word_vectors), axis=1) #, description_vectors, word_vectors

# put game id on master_games DF
master_games['BGGId'] = game_ids

# set index to id
master_games.set_index('BGGId', inplace=True)

#master_games.head()

In [ ]:
master_games.to_pickle('data_cleaned_new_scraper/master_games_scaled.pkl')

In [ ]:
'''# clean up

del mechanics
del designers
del subcategories
del themes
del scaled_mechanics
del scaled_families
del scaled_designers
del scaled_games
del scaled_subcategories
del scaled_themes
del description_vectors

gc.collect()'''

## Item Similarity via Cosine Distance

In [4]:
master_games = pd.read_pickle('data_cleaned_new_scraper/master_games_scaled.pkl')

In [99]:
# Load games
games = pd.read_pickle('data_cleaned_new_scraper/games.pkl')

# get list of game ids
game_ids = list(games['BGGId'])

game_names = list(games['Name'].str.lower())

In [100]:
# get cosine similarities!
cosine_sims = cosine_similarity(master_games)

# do similarities by game id
sims_byid = pd.DataFrame(cosine_sims, columns=game_ids)
sims_byid['Game_Id'] = game_ids
sims_byid.set_index('Game_Id', inplace=True, drop=True)

In [101]:
# SCALE IF NEEDED

threshold = .95

sims_byid = sims_byid.round(6)

for column in list(sims_byid.columns):
    lower = sims_byid[column].min()
    sims_byid[column].replace(1.,lower, inplace=True)
    if sims_byid[column].max() > threshold:
        continue
    else:
        scaler = MinMaxScaler(feature_range=(lower, threshold))
        scaled_values = scaler.fit_transform(np.array(sims_byid[column]).reshape(-1,1))
        sims_byid[column] = scaled_values

In [102]:
sims_byid = sims_byid.round(2)
sims_byid.head()

1     2     3     4     5     6     7     8     9    10    11  \
Game_Id                                                                     
1        0.35  0.56  0.65  0.74  0.74  0.85  0.48  0.76  0.76  0.61  0.60   
2        0.58  0.46  0.67  0.69  0.71  0.64  0.66  0.72  0.67  0.67  0.72   
3        0.65  0.64  0.47  0.76  0.74  0.62  0.64  0.66  0.80  0.64  0.65   
4        0.73  0.67  0.77  0.48  0.70  0.69  0.65  0.72  0.76  0.64  0.64   
5        0.70  0.66  0.71  0.66  0.46  0.73  0.62  0.73  0.74  0.66  0.63   

           12    13    14    15    16    17    18    19    20    21    22  \
Game_Id                                                                     
1        0.64  0.66  0.67  0.76  0.74  0.47  0.62  0.56  0.70  0.52  0.83   
2        0.67  0.61  0.74  0.66  0.78  0.71  0.60  0.74  0.66  0.71  0.56   
3        0.70  0.61  0.70  0.66  0.68  0.62  0.56  0.73  0.68  0.65  0.55   
4        0.78  0.60  0.73  0.66  0.83  0.65  0.59  0.69  0.78  0.71  0.61   
5        0.64  0.63  0.65  0.70  0.75  0.60  0.60  0.72  0.67  0.62  0.65   

           23    24    25    26    27    28    29    30    31    32    34  \
Game_Id                                                                     
1        0.73  0.78  0.76  0.86  0.78  0.80  0.75  0.66  0.66  0.51  0.76   
2        0.56  0.55  0.59  0.60  0.59  0.73  0.67  0.71  0.70  0.70  0.62   
3        0.57  0.61  0.62  0.60  0.56  0.66  0.63  0.63  0.63  0.62  0.59   
4        0.59  0.59  0.63  0.74  0.65  0.65  0.80  0.72  0.67  0.64  0.68   
5        0.63  0.66  0.66  0.70  0.67  0.73  0.70  0.69  0.68  0.62  0.69   

           36    37    38    39    40    41    42    43    44    45    46  \
Game_Id                                                                     
1        0.75  0.70  0.53  0.64  0.75  0.56  0.74  0.68  0.61  0.50  0.67   
2        0.55  0.68  0.68  0.69  0.62  0.74  0.64  0.69  0.91  0.69  0.70   
3        0.58  0.63  0.62  0.67  0.57  0.66  0.83  0.64  0.64  0.61  0.73   
4        0.60  0.67  0.64  0.71  0.63  0.68  0.74  0.67  0.67  0.61  0.79   
5        0.64  0.68  0.62  0.63  0.65  0.70  0.85  0.78  0.67  0.62  0.67   

           47    48    49    50    51    52    53    54    55    57    58  \
Game_Id                                                                     
1        0.70  0.76  0.53  0.54  0.51  0.74  0.58  0.73  0.67  0.83  0.68   
2        0.71  0.69  0.74  0.79  0.64  0.61  0.75  0.61  0.72  0.63  0.59   
3        0.75  0.66  0.62  0.74  0.58  0.58  0.67  0.82  0.65  0.60  0.64   
4        0.77  0.80  0.61  0.69  0.60  0.63  0.71  0.89  0.73  0.74  0.67   
5        0.76  0.69  0.62  0.65  0.59  0.74  0.68  0.70  0.70  0.73  0.65   

           59    60    61    62    63    64    66    67    68    69    70  \
Game_Id                                                                     
1        0.70  0.76  0.54  0.74  0.73  0.76  0.84  0.68  0.74  0.53  0.64   
2        0.66  0.64  0.70  0.72  0.58  0.62  0.69  0.63  0.59  0.68  0.70   
3        0.61  0.68  0.70  0.66  0.58  0.63  0.75  0.60  0.56  0.61  0.75   
4        0.74  0.74  0.73  0.75  0.61  0.63  0.86  0.76  0.63  0.67  0.68   
5        0.68  0.77  0.63  0.74  0.65  0.64  0.71  0.66  0.65  0.61  0.75   

           71    72    73    74    75    76    77    78    79    82    83  \
Game_Id                                                                     
1        0.84  0.65  0.66  0.55  0.45  0.81  0.71  0.72  0.70  0.72  0.71   
2        0.56  0.78  0.77  0.71  0.77  0.69  0.56  0.56  0.55  0.58  0.59   
3        0.66  0.67  0.68  0.60  0.61  0.70  0.58  0.58  0.57  0.56  0.56   
4        0.68  0.65  0.78  0.58  0.60  0.79  0.60  0.61  0.59  0.62  0.63   
5        0.68  0.68  0.66  0.60  0.59  0.82  0.62  0.63  0.61  0.64  0.65   

           84    85    87    88    89    90    91    93    94    95    96  \
Game_Id                                                                     
1        0.70  0.58  0.70  0.64  0.75  0.54  0.74  0.73  0.68  0.53  0.66   
2

In [103]:
for item in np.arange(0, len(game_names), 1):
    game_names[item] = re.sub('[^A-Za-z0-9\s]+', '', game_names[item])

In [104]:
sims_byname = sims_byid.copy()
sims_byname.set_axis(game_names, axis=1, inplace=True)
sims_byname.set_axis(game_names, axis=0, inplace=True)

In [109]:
# save to pickles, we really only need the id one
sims_byid.to_pickle('data_cleaned_new_scraper/game_cosine_similarity_byid.pkl')
sims_byname.to_pickle('data_cleaned_new_scraper/game_cosine_similarity_byname.pkl')

### CHECK GAME HERE

In [34]:
# save to pickles, we really only need the id one
sims_byid = pd.read_pickle('data_cleaned_new_scraper/game_cosine_similarity_byid.pkl')
sims_byname = pd.read_pickle('data_cleaned_new_scraper/game_cosine_similarity_byname.pkl')

This is why we made the name one

In [105]:
# test my specific game set here

test_dict = {'Dominion':list(sims_byname['dominion'].sort_values(ascending=False)[:15].index), 'D_Sim':list(sims_byname['dominion'].sort_values(ascending=False)[:15]),
            'Gloomhaven':list(sims_byname['gloomhaven'].sort_values(ascending=False)[:15].index), 'G_Sim':list(sims_byname['gloomhaven'].sort_values(ascending=False)[:15]),
            'Pandemic':list(sims_byname['pandemic'].sort_values(ascending=False)[:15].index), 'Pa_Sim':list(sims_byname['pandemic'].sort_values(ascending=False)[:15]),
            'Splendor':list(sims_byname['splendor'].sort_values(ascending=False)[:15].index), 'Sp_Sim':list(sims_byname['splendor'].sort_values(ascending=False)[:15]),
            'Viticulture Essential Edition':list(sims_byname['viticulture essential edition'].sort_values(ascending=False)[:15].index), 'V_Sim':list(sims_byname['viticulture essential edition'].sort_values(ascending=False)[:15]),
            'Agricola':list(sims_byname['agricola'].sort_values(ascending=False)[:15].index), 'Ag_Sim':list(sims_byname['agricola'].sort_values(ascending=False)[:15]),
             'Space Base':list(sims_byname['space base'].sort_values(ascending=False)[:15].index), 'Spa_Sim':list(sims_byname['space base'].sort_values(ascending=False)[:15]),
             'Terraforming Mars':list(sims_byname['terraforming mars'].sort_values(ascending=False)[:15].index), 'Te_Sim':list(sims_byname['terraforming mars'].sort_values(ascending=False)[:15]),
            #'Puerto Rico':list(sims_byname['Puerto Rico'].sort_values(ascending=False)[:15].index), 'Pu_Sim':list(sims_byname['Puerto Rico'].sort_values(ascending=False)[:15]),
            'Chess':list(sims_byname['chess'].sort_values(ascending=False)[:15].index), 'Ch_Sim':list(sims_byname['chess'].sort_values(ascending=False)[:15]),
            #'Backgammon':list(sims_byname['Backgammon'].sort_values(ascending=False)[:15].index), 'B_Sim':list(sims_byname['Backgammon'].sort_values(ascending=False)[:15]),
            #'Sagrada':list(sims_byname['Sagrada'].sort_values(ascending=False)[:15].index), 'Sa_Sim':list(sims_byname['Sagrada'].sort_values(ascending=False)[:15]),
            'Azul':list(sims_byname['azul'].sort_values(ascending=False)[:15].index), 'Az_Sim':list(sims_byname['azul'].sort_values(ascending=False)[:15]),
            'Codenames':list(sims_byname['codenames'].sort_values(ascending=False)[:15].index), 'Co_Sim':list(sims_byname['codenames'].sort_values(ascending=False)[:15]),
            'Secret Hitler':list(sims_byname['secret hitler'].sort_values(ascending=False)[:15].index), 'Se_Sim':list(sims_byname['secret hitler'].sort_values(ascending=False)[:15]),
            'Monopoly':list(sims_byname['monopoly'].sort_values(ascending=False)[:15].index), 'M_Sim':list(sims_byname['monopoly'].sort_values(ascending=False)[:15]), 
            'Lords of Waterdeep':list(sims_byname['lords of waterdeep'].sort_values(ascending=False)[:15].index), 'L_Sim':list(sims_byname['lords of waterdeep'].sort_values(ascending=False)[:15]),
            'Stone Age':list(sims_byname['stone age'].sort_values(ascending=False)[:15].index), 'St_Sim':list(sims_byname['stone age'].sort_values(ascending=False)[:15]),
            'Century: Spice Road':list(sims_byname['century spice road'].sort_values(ascending=False)[:15].index), 'Ce_Sim':list(sims_byname['century spice road'].sort_values(ascending=False)[:15]),
            #'Scrabble':list(sims_byname['Scrabble'].sort_values(ascending=False)[:15].index), 'Sc_Sim':list(sims_byname['Scrabble'].sort_values(ascending=False)[:15]),
            '18MS: The Railroads Come to Mississippi':list(sims_byname['18ms the railroads come to mississippi'].sort_values(ascending=False)[:15].index), '18xx':list(sims_byname['18ms the railroads come to mississippi'].sort_values(ascending=False)[:15]),
             #'Roads to Gettysburg II: Lee Strikes North':list(sims_byname['Roads to Gettysburg II: Lee Strikes North'].sort_values(ascending=False)[:15].index), 'War3':list(sims_byname['Roads to Gettysburg II: Lee Strikes North'].sort_values(ascending=False)[:15]),
             'Power Grid':list(sims_byname['power grid'].sort_values(ascending=False)[:15].index), 'P_Grid':list(sims_byname['power grid'].sort_values(ascending=False)[:15]),
            }

pd.DataFrame(test_dict)

Dominion  D_Sim  \
0          dominion special edition   0.95   
1           dominion second edition   0.94   
2          dominion big box english   0.91   
3                 dominion intrigue   0.90   
4         dominion einsteigerbigbox   0.84   
5   dominion second edition big box   0.84   
6           het koninkrijk dominion   0.84   
7           dominion big box german   0.84   
8             the valkyrie incident   0.81   
9                              fort   0.81   
10                      guns  steel   0.81   
11                   pentaurus duel   0.81   
12                       outpost 18   0.81   
13                       mythotopia   0.81   
14                           cuttle   0.80   

                                       Gloomhaven  G_Sim  \
0                     gloomhaven jaws of the lion   0.95   
1              middara unintentional malum  act 1   0.83   
2   middara unintentional malum  act 1 version 11   0.83   
3                                     etherfields   0.83   
4   the lord of the rings journeys in middleearth   0.81   
5                                       star saga   0.81   
6                       bloodborne the board game   0.80   
7                          mage knight board game   0.80   
8                              exo mankind reborn   0.80   
9                                dungeon alliance   0.79   
10            warhammer quest blackstone fortress   0.79   
11                      dark souls the board game   0.79   
12                   mage knight ultimate edition   0.78   
13                                     cloudspire   0.78   
14                               galaxy defenders   0.78   

                                         Pandemic  Pa_Sim  \
0                        pandemic legacy season 1    0.95   
1                                 pandemic iberia    0.90   
2        world of warcraft wrath of the lich king    0.90   
3                       pandemic reign of cthulhu    0.90   
4                pandemic hot zone  north america    0.87   
5                        pandemic legacy season 0    0.87   
6                       pandemic hot zone  europe    0.87   
7                           pandemic fall of rome    0.86   
8                                 kings of israel    0.85   
9                        pandemic legacy season 2    0.84   
10                              pandemic the cure    0.84   
11                             mole rats in space    0.79   
12                     alien fate of the nostromo    0.79   
13               double mission beyond the object    0.78   
14  squire the collector of the glorious rarities    0.78   

                          Splendor  Sp_Sim  \
0                  splendor marvel    0.95   
1                             chai    0.89   
2                           gizmos    0.86   
3                quests of valeria    0.85   
4                       port royal    0.84   
5   taco bell party pack card game    0.82   
6                       gelato mio    0.82   
7                       res arcana    0.82   
8                             amul    0.82   
9                 saint petersburg    0.82   
10                        ganymede    0.81   
11           splendor asmoplay kit    0.81   
12                       elementum    0.81   
13                  7 wonders duel    0.81   
14                         vidrado    0.81   

              Viticulture Essential Edition  V_Sim  \
0                               viticulture   0.95   
1   viticulture complete collectors edition   0.81   
2                        raiders of scythia   0.81   
3                                 hallertau   0.80   
4                  raiders of the north sea   0.80   
5                                 corrosion   0.80   
6                              charterstone   0.79   
7                       ore the mining game   0.79   
8                    at the gates of loyang   0.79   
9                 alubari a nice cup of tea   0.79   
10                   

In [108]:
# test specific games here
game = 'mariposas'
game = game.lower()

results = pd.DataFrame(data={'Similarity': sims_byname[game].sort_values(ascending=False)[0:21]})
results.index = results.index.str.title()
results

Similarity
The Baton Races Of Yaz                        0.95
Gorogoro Dbutsu Shgi                          0.94
Wind  Wetter                                  0.93
Rare Roses                                    0.93
Fenix                                         0.93
Star Explorer                                 0.93
Musical Chairs                                0.93
Counter Attack                                0.93
Survival  The Barbarian                       0.93
Formosa Flowers                               0.92
Zaubertrank Der Vier Elemente                 0.92
Animals On Board                              0.92
Deblockle                                     0.92
Tour Operator                                 0.91
Biyi                                          0.91
Pusheen Purrfect Pick                         0.91
Wind River                                    0.91
Mystical Seeds                                0.91
Bundeswehr Northern Germany Late 1970S        0.91
Crash Tackle Rugby Board Game                 0.91
Liebe  Intrige                                0.90

# Appendix

## Glove Word Embeddings

In [12]:
# amount of vocabulary to use, will pick the top 10000 words seen in the corpus
features = 5000

# max text sequence length, must match tokens in transfer file, we are using glove 300d so it is 300
max_words = 300

'# amount of vocabulary to use, will pick the top 10000 words seen in the corpus\nfeatures = 5000\n\n# max text sequence length, must match tokens in transfer file, we are using glove 300d so it is 300\nmax_words = 300'

In [13]:
# instantiate our word tokenizer
tokenizer = Tokenizer(num_words=features)

# Create vocabulary with training texts
tokenizer.fit_on_texts(games['Description']) # nltk method which creates a vocab index based on the word frequency, every word gets own integer value

# pad the train text to 300, or cut off if over
tokenized_train = tokenizer.texts_to_sequences(games['Description'])# transforms each text to a sequence of integers
tokenized_train = sequence.pad_sequences(tokenized_train, maxlen=max_words, truncating='post',padding='post') #truncates or pads the vector to the max_words


"# instantiate our word tokenizer\ntokenizer = Tokenizer(num_words=features)\n\n# Create vocabulary with training texts\ntokenizer.fit_on_texts(games['Description']) # nltk method which creates a vocab index based on the word frequency, every word gets own integer value\n\n# pad the train text to 300, or cut off if over\ntokenized_train = tokenizer.texts_to_sequences(games['Description'])# transforms each text to a sequence of integers\ntokenized_train = sequence.pad_sequences(tokenized_train, maxlen=max_words, truncating='post',padding='post') #truncates or pads the vector to the max_words\n"

In [14]:
# identify the embedding filename; we are using the Glove 42B 300d embeddings
glove_file = "glove.42B.300d.txt"

# create the embeddings index dictionary
embeddings_index = {} # create a lookup dictionary to store words and their vectors
f = open(glove_file, errors='ignore')# open our embedding file 
for line in f: # for each line in the file
    values = line.split(' ') #split the line on spaces between the word and its vectors
    word = values[0] # the word is the first entry
    if word in tokenizer.word_index.keys(): # we check if the word is in our tokenizer word index
        coefs = np.asarray(values[1:], dtype='float32') # if so, get the word's vectors
        embeddings_index[word] = coefs # add the word and its vectors to the embeddings_index dictionary
f.close()

print('Found %s word vectors.' % len(embeddings_index)) # report how many words in our corpus were found in the GloVe words


'# identify the embedding filename; we are using the Glove 42B 300d embeddings\nglove_file = "glove.42B.300d.txt"\n\n# create the embeddings index dictionary\nembeddings_index = {} # create a lookup dictionary to store words and their vectors\nf = open(glove_file, errors=\'ignore\')# open our embedding file \nfor line in f: # for each line in the file\n    values = line.split(\' \') #split the line on spaces between the word and its vectors\n    word = values[0] # the word is the first entry\n    if word in tokenizer.word_index.keys(): # we check if the word is in our tokenizer word index\n        coefs = np.asarray(values[1:], dtype=\'float32\') # if so, get the word\'s vectors\n        embeddings_index[word] = coefs # add the word and its vectors to the embeddings_index dictionary\nf.close()\n\nprint(\'Found %s word vectors.\' % len(embeddings_index)) # report how many words in our corpus were found in the GloVe words\n'

In [15]:
num_tokens = (len(tokenizer.word_index) + 1) # for num tokens we always do the length of our word index +1 for a pad token
hits = 0
misses = 0

embedding_matrix = np.zeros((num_tokens, max_words)) # setting up an array for our tokens with a row per token and 300 columns
for word, i in tokenizer.word_index.items(): # for each word in the tokenizer word index
    embedding_vector = embeddings_index.get(word) #get the vector from the embeddings index dictionary
    if embedding_vector is not None: # if the vector isn't None,
        # words not found in embedding index will be all-zeros.
        embedding_matrix[i] = embedding_vector # store the embedding vector in the matrix at that index
        hits += 1
    else:
        misses += 1
        
print("Converted %d words (%d misses)" % (hits, misses))


'num_tokens = (len(tokenizer.word_index) + 1) # for num tokens we always do the length of our word index +1 for a pad token\nhits = 0\nmisses = 0\n\nembedding_matrix = np.zeros((num_tokens, max_words)) # setting up an array for our tokens with a row per token and 300 columns\nfor word, i in tokenizer.word_index.items(): # for each word in the tokenizer word index\n    embedding_vector = embeddings_index.get(word) #get the vector from the embeddings index dictionary\n    if embedding_vector is not None: # if the vector isn\'t None,\n        # words not found in embedding index will be all-zeros.\n        embedding_matrix[i] = embedding_vector # store the embedding vector in the matrix at that index\n        hits += 1\n    else:\n        misses += 1\n        \nprint("Converted %d words (%d misses)" % (hits, misses))\n'

### Single Testing

In [16]:
temp = games[:5]

In [17]:
vector_storage = {}

In [18]:
temp.apply(lambda x: vectorize(x), axis=1)

In [19]:
pd.DataFrame(vector_storage).T

### Real Word Vectors

In [20]:
def vectorize(x):
    
    description = x['Description']
    
    tokens = nlp(description)
    
    vector_storage[x['BGGId']] = {}
    
    for token in tokens:
        
        word = str(token)
        
        try:
            if np.all(embedding_matrix[tokenizer.word_index[word]]):
                vector_storage[x['BGGId']][word] = np.mean(embedding_matrix[tokenizer.word_index[word]])
            else: continue
        except: continue

In [21]:
vector_storage = {}

In [22]:
descriptions = games[['BGGId', 'Description']]

In [23]:
descriptions.apply(lambda x: vectorize(x), axis=1)

In [24]:
description_vectors = pd.DataFrame(vector_storage).T

In [25]:
description_vectors.shape

In [26]:
# Get only vectors that show up more than once!
refined_vectors = description_vectors.loc[:, (description_vectors.isnull().sum(axis=0) <= 21923)]

In [27]:
refined_vectors.fillna(0, inplace=True)
refined_vectors.reset_index(inplace=True)
refined_vectors.drop('level_0', axis=1, inplace=True)

In [28]:
refined_vectors.to_pickle('data_cleaned_new_scraper/description_vectors.pkl')

In [29]:
del vector_storage
del refined_vectors
del embedding_matrix
del tokenizer
del descriptions
del embedding_vector

gc.collect()

'del vector_storage\ndel refined_vectors\ndel embedding_matrix\ndel tokenizer\ndel descriptions\ndel embedding_vector\n\ngc.collect()'